In [1]:
from bokeh.plotting import figure
from bokeh.io import show, output_notebook
from bokeh.layouts import column, row
from bokeh.models import Range1d
output_notebook()

import numpy as np

from voltagebudget import util
from voltagebudget import neurons
from voltagebudget.budget import locate_first
from voltagebudget.budget import filter_voltages
from fakespikes import util as fsutil

Loading BokehJS ...

# Define input

In [68]:
t = 1.0

k = 50
stim_onset = 0.6
stim_offset = 0.630
stim_rate = 12
dt = 1e-5
seed_stim = 1
ns, ts = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=k,
        dt=dt,
        seed=seed_stim)

print(">>> {} spikes".format(ts.size))
print(">>> {} population rate".format(ts.size / (stim_offset - stim_onset)))

>>> 15 spikes
>>> 500.0 population rate


In [69]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts*1e3, ns, color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.x_range = Range1d(0, 1000)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

- Shadow voltage response of an LIF neuron to the input

In [70]:
#set mode
mode = 'regular'
params, w_max, bias, sigma = util.read_modes(mode)

In [71]:
sigma

3e-09

In [72]:
# -
v_in, b_in = neurons.shadow_adex(1, t, ns, ts, w_max=w_max, bias=bias, sigma=sigma, **params)

times = b_in['times']
m = times > 0.05  # Burn in time

# -
p = figure(plot_width=400, plot_height=200)
p.line(x=times[m], y=v_in[0, :][m], color="black")
p.x_range = Range1d(0, t)
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

Starting simulation at t=0. s for a duration of 1. s
1. s (100%) simulated in 1s


WARNING    Came across an abstract code block that may not be well-defined: the outcome may depend on the order of execution. You can ignore this warning if you are sure that the order of operations does not matter. 2 lines of abstract code, first line is: "g_in += w_max * rand() (in-place)"
 [brian2.codegen.generators.base]


Starting simulation at t=0. s for a duration of 1. s
1. s (100%) simulated in 1s


# Define computational models

And obseve how they respond to the same input

## Regular

In [73]:
ns_y, ts_y, budget = neurons.adex(50, t, ns, ts, 
                                  w_max=w_max, 
                                  bias=bias, 
                                  sigma=sigma, 
                                  A=.0, f=0, **params)

Starting simulation at t=0. s for a duration of 1. s
1. s (100%) simulated in 1s


WARNING    Came across an abstract code block that may not be well-defined: the outcome may depend on the order of execution. You can ignore this warning if you are sure that the order of operations does not matter. 2 lines of abstract code, first line is: "g_in += w_max * rand() (in-place)"
 [brian2.codegen.generators.base]


Starting simulation at t=0. s for a duration of 1. s
1. s (100%) simulated in 1s


In [74]:
bias

5.8129317905916417e-11

In [75]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts_y, ns_y, color="black")
p.x_range = Range1d(0.0, t)
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

print(ts_y.size)

0


In [9]:
times = budget['times']
m = times > 0.05  # Burn in time

p = figure(plot_width=400, plot_height=200)
for n in range(20):
    v = budget['V_m'][n, :]
    p.line(x=times[m], y=v[m], color="black", alpha=0.1)
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [59]:
# Extract budgets
combine = False
ns_first, ts_first = locate_first(ns_y, ts_y, combine=combine)
voltages_m = filter_voltages(
    budget,
    ns_first,
    ts_first,
    budget_delay=-10e-3,
    budget_width=2e-3,
    combine=combine)

times = budget['times']


p = figure(plot_width=400, plot_height=200)

for n in range(20):
    v = voltages_m['V_m'][n, :]
    if not combine:
        times = voltages_m['times'][n, :]
    else:
        times = voltages_m['times']
    
    p.line(x=times, y=v, color="purple", alpha=0.8)
    
    v_full = budget['V_m'][n, :]
    times_full = budget['times']
    p.line(x=times_full, y=v_full, color="black", alpha=0.1)
    
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.x_range = Range1d(0.63, 0.7)
p.y_range = Range1d(-66e-3, -30e-3)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [31]:
print(voltages_m['V_m'].shape, voltages_m['times'].shape)

((20, 21), (21,))


In [11]:
times = budget['times']
v = budget['V_comp'][0, :]
m = times > 0.05  # Burn in time

p = figure(plot_width=400, plot_height=200)
p.line(x=times[m], y=v[m], color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [12]:
times = budget['times']
v = budget['V_osc'][0, :]
m = times > 0.05  # Burn in time

p = figure(plot_width=400, plot_height=200)
p.line(x=times[m], y=v[m], color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [13]:
times = budget['times']
v = budget['V_free'][0, :]
m = times > 0.05  # Burn in time

p = figure(plot_width=400, plot_height=200)
p.line(x=times[m], y=v[m], color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)